Assignment 1 - Data Analytics
Andrew Spiro (s4015355) and Elena Petridou (s2029197)

Please note: on some machines we have encountered an error with the pd.to_datetime() command. If you also encounter it,
we found that adding format = 'mixed' as an argument solves it. However, if the error is not encountered, the argument
gives another error.

Only use the above argument if you encounter this error, at the lines indicated by the comment: # Note: if this cell doesn't run please try adding format = 'mixed' as an argument to pd.datetime()

In [3]:
# Import Statements
# !pip install currencyconverter
import pandas as pd
import geopandas as gpd
import json
import matplotlib as mpl
import pylab as plt
import numpy as np
import glob
import os
import panel as pn
import panel.widgets as pnw
import colorcet as cc


from IPython.display import display
from bokeh.io import output_file, show, output_notebook, export_png
from bokeh.layouts import row, column as bokeh_column, gridplot, layout
from bokeh.models import ColumnDataSource, GeoJSONDataSource, LinearColorMapper, ColorBar, Slider, CustomJS, DateSlider, HoverTool, CustomJSTickFormatter, Tabs, TabPanel
from bokeh.plotting import figure
from bokeh.palettes import brewer
from datetime import datetime, date

from bokeh.models import HoverTool, LinearAxis, DataRange1d, Range1d

from currency_converter import CurrencyConverter, RateNotFoundError





ModuleNotFoundError: No module named 'panel'

In [ ]:
from bokeh.models import Div

In [ ]:
# Create empty dataframes for each attribute
dataframes = {"reviews": [], "stats_crashes": [], "sales": [], "ratings": [], "ratings_per_country":[]}

In [ ]:
# FUNCTION TO LOAD IN DATA
c = CurrencyConverter()



# Helper function to deal with encoding issues
def read_encoded_csv(filename):
  try:
    frame = pd.read_csv(filename, header = 0, encoding = 'utf-16')
  except:
    frame = pd. read_csv(filename, header = 0, encoding = 'utf-8')
  return frame


# Helper function to deal with the different columns in sales November & December
'''Please note: the exchange rates for some currencies were hard-coded due to official exchange rate
  for the EURO not being available on the ECB website (and hence also not in the currency_converter package)
  Sources: https://www.exchange-rates.org/exchange-rate-history/cop-eur-2021
  https://www.exchange-rates.org/exchange-rate-history/ghs-eur-2021
  https://www.exchange-rates.org/exchange-rate-history/crc-eur-2021
  '''
def november_december(filename, dataframes_dict):
  merchant_currency = []
  manual_rates = {"COP":0.0002, "GHS": 0.143, "CRC":0.0013}
  c = CurrencyConverter()
  frame = read_encoded_csv(filename)
  frame = frame.loc[:,["Order Charged Date", "Product Title",	"SKU ID", "Currency of Sale", "Item Price", "Country of Buyer", "Product ID"]]
  for row in frame.itertuples():
    price = row[5]
    sales_currency = row[4]
    date_to_search = [int(i) for i in row[1].split("-")]
    year = date_to_search[0]
    month = date_to_search[1]
    day = date_to_search[2]
    try:
      new_currency = c.convert(price, sales_currency, 'EUR', date=date(year, month, day))
    except ValueError:
      new_currency = float(price.replace(',','')) * manual_rates[sales_currency]
    except RateNotFoundError:
      try:
        c.convert(price, sales_currency, 'EUR', date = date(year, month, day-1))
      except RateNotFoundError:
        c.convert(price, sales_currency, 'EUR', date = date(year,month, day-2))
    merchant_currency.append(new_currency)
  frame["Amount (Merchant Currency)"] = merchant_currency
  frame = frame.rename(columns = {"Order Charged Date": "Transaction Date", "SKU ID": "Sku Id", "Country of Buyer": "Buyer Country", "Product ID": "Product id"})
  dataframes_dict["sales"].append(frame)


def remove_google_charges(filename, dataframe_dict):
  frame = read_encoded_csv(filename)
  new_frame = frame[frame["Transaction Type"] == "Charge"]
  dataframe_dict["sales"].append(new_frame)



def open_datasets(variable):
  for filename in os.listdir():
    # This conditional is to make sure that no unrelated file in the directory is accidentally included
    key = variable
    if variable in filename:
    # Ratings per country need the variable to be custom
      if "country" in filename and "ratings" in filename:
        key = "ratings_per_country"
      elif "sales" in filename and ("202111" in filename or "202112" in filename):
         november_december(filename, dataframes)
         continue
      elif "sales" in filename and not ("202111" in filename or "202112" in filename):
        remove_google_charges(filename, dataframes)
        continue
      frame = read_encoded_csv(filename)
      dataframes[key].append(frame)
  concatenated_frame = pd.concat(dataframes[key], axis = 0, ignore_index = True)
  return concatenated_frame




reviews = open_datasets("reviews")
sales = open_datasets("sales")
crash_stats = open_datasets("stats_crashes")
ratings_per_day = open_datasets("ratings")
per_country = open_datasets("ratings_per_country")

sales_sorted = sales.sort_values(by = "Transaction Date", ascending = False)
reviews = reviews[reviews["Package Name"] == "com.vansteinengroentjes.apps.ddfive"]
sales = sales[sales["Product id"] == "com.vansteinengroentjes.apps.ddfive"]
crash_stats = crash_stats[crash_stats["Package Name"] == "com.vansteinengroentjes.apps.ddfive"]
ratings_per_day = ratings_per_day[ratings_per_day["Package Name"] == "com.vansteinengroentjes.apps.ddfive"]
per_country = per_country[per_country["Package Name"]== "com.vansteinengroentjes.apps.ddfive"]


In [ ]:
# IMPORTING COUNTRY CODES
country_codes = pd.read_csv('country_codes.csv')
country_codes = country_codes[["alpha-3", "name", 'alpha-2', 'region']]

In [ ]:
#Global variables
palette=brewer['Dark2'][8][::-1]
figure_height = 450
figure_width = 700

#**SALES VOLUME**

In [ ]:
sales.head()

Transaction Date                                     Product Title  \
2       2021-11-01  Character Manager (Complete Reference for DnD 5)   
3       2021-11-01  Character Manager (Complete Reference for DnD 5)   
4       2021-11-01           DM Tools (Complete Reference for DnD 5)   
5       2021-11-01  Character Manager (Complete Reference for DnD 5)   
6       2021-11-02  Character Manager (Complete Reference for DnD 5)   

                   Sku Id Currency of Sale Item Price Buyer Country  \
2  unlockcharactermanager              USD       5.49            US   
3  unlockcharactermanager              EUR       4.19            DE   
4                 premium              GBP       2.16            GB   
5  unlockcharactermanager              GBP       3.49            GB   
6  unlockcharactermanager              USD       5.49            US   

                            Product id  Amount (Merchant Currency)  \
2  com.vansteinengroentjes.apps.ddfive                    4.741752   
3  com.vansteinengroentjes.apps.ddfive                    4.190000   
4  com.vansteinengroentjes.apps.ddfive                    2.553946   
5  com.vansteinengroentjes.apps.ddfive                    4.126515   
6  com.vansteinengroentjes.apps.ddfive                    4.731535   

  Description Transaction Time  ... Product Type Hardware Buyer State  \
2         NaN              NaN  ...          NaN      NaN         NaN   
3         NaN              NaN  ...          NaN      NaN         NaN   
4         NaN              NaN  ...          NaN      NaN         NaN   
5         NaN              NaN  ...          NaN      NaN         NaN   
6         NaN              NaN  ...          NaN      NaN         NaN   

   Buyer Postal Code Buyer Currency Amount (Buyer Currency)  \
2                NaN            NaN                     NaN   
3                NaN            NaN                     NaN   
4                NaN            NaN                     NaN   
5                NaN            NaN                     NaN   
6                NaN            NaN                     NaN   

  Currency Conversion Rate Merchant Currency  Base Plan ID  Offer ID  
2                      NaN               NaN           NaN       NaN  
3                      NaN               NaN           NaN       NaN  
4                      NaN               NaN           NaN       NaN  
5                      NaN               NaN           NaN       NaN  
6                      NaN               NaN           NaN       NaN  

[5 rows x 23 columns]

In [ ]:
# SALES VOLUME DATA PROCESSING

sales_vol = sales[sales['Transaction Date'].notna()].loc[:,['Transaction Date','Amount (Merchant Currency)']]
sales_vol['Transaction Date'] = pd.to_datetime(sales_vol['Transaction Date']) # Note: if this cell doesn't run please try adding format = 'mixed' as an argument to pd.datetime()
sales_amount = sales_vol.groupby('Transaction Date').sum(numeric_only = True)
sales_count = sales_vol.groupby('Transaction Date').count()


In [ ]:
# SALES VOLUME PLOTTING
output_notebook()
tools = "pan,wheel_zoom,box_zoom,reset"
tooltips_amount = [('Amount','@{Amount (Merchant Currency)}'), ('Date', '@{Transaction Date}{%F}')]
tooltips_count = [('Count','@{Amount (Merchant Currency)}'), ('Date', '@{Transaction Date}{%F}')]
sales_vol_fig = figure(title = "Sales per Day", x_axis_label="Day", y_axis_label="Amount (EUR)", height=figure_height, width=figure_width, x_axis_type = 'datetime', tools=tools)

amount_fig = sales_vol_fig.line(source=sales_amount, x = 'Transaction Date', y='Amount (Merchant Currency)',color=palette[5],legend_label='Daily amount',muted_alpha=0.1)

# count_fig = sales_vol_fig.line(source=sales_count, x = 'Transaction Date', y='Amount (Merchant Currency)')
# sales_vol_fig.extra_y_ranges['count'] = DataRange1d(renderers = [count_fig])
sales_vol_fig.extra_y_ranges['count'] = Range1d(start =float(sales_count.min())*0.9, end =float(sales_count.max())*1.1)
count_fig = sales_vol_fig.line(y_range_name = 'count', source=sales_count, x = 'Transaction Date', y='Amount (Merchant Currency)', color=palette[3],legend_label='Daily transactions',muted_alpha=0.1)


sales_vol_fig.yaxis.axis_label = "Amount per day (EUR)"
sales_vol_fig.yaxis.axis_label_text_color = palette[5]

count_axis = LinearAxis(y_range_name="count",axis_label_text_color = palette[3],axis_label = "Number of transactions per day")
sales_vol_fig.add_layout(count_axis,"left")

sales_vol_fig.xaxis.axis_label = "Date"

sales_vol_fig.add_tools(HoverTool(tooltips=tooltips_amount, renderers=[amount_fig], formatters={"@{Transaction Date}":"datetime"}))
sales_vol_fig.add_tools(HoverTool(tooltips=tooltips_count, renderers=[count_fig], formatters={"@{Transaction Date}":"datetime"}))
sales_vol_fig.legend.click_policy = 'hide'
sales_vol_fig.legend.location = 'top_left'
show(sales_vol_fig)

In [ ]:
sales_vol_panel = TabPanel(child = sales_vol_fig,title = 'Sales per Day')

**MAKING THE CHOROPLETHS FOR GEOGRAPHICAL DEVELOPMENT**

In [ ]:
# OPENING THE RATINGS PER COUNTRY DATA PER MONTH
'''
  The ratings per country are entered "per day" but most cells are empty. Thus, we need only the monthly rating,
  but need to first put the datasets together with country as a column and rows the dates, to ensure that the monthly
  rating value is the same throughout all days.

  This is a different structure to the other datasets, and so requires its own function.
'''

months = {"202106": ["June"], "202107": ["July"], "202108": ["August"], "202109": ["September"], "202110": ["October"], "202111": ["November"],
          "202112": ["December"]}

def opening_country_ratings():
  # Create empty dataframe and add Countries as the index, to fill in with data
  country_ratings_per_month = pd.DataFrame()
  country_ratings_per_month["Country"] = country_codes['alpha-2']
  i = 0
  for filename in os.listdir():
    if "ratings" in filename and "country" in filename:
      for key, value in months.items():
        condition = filename.find(key)
        if condition != -1:
          date = key
          month = value
          temp_df = read_encoded_csv(filename)
          temp_df = temp_df[["Country", "Total Average Rating", "Date"]]
          temp_df.set_index("Date", inplace = True)
          rating_per_day = pd.pivot_table(temp_df, values = "Total Average Rating", index = "Date", columns = "Country", aggfunc = "mean")
          mean_ratings = rating_per_day.mean(axis = 0)
          mean_ratings_df = pd.DataFrame(mean_ratings, columns = ["Average Rating"])
          country_ratings_per_month = country_ratings_per_month.join(mean_ratings_df, on = 'Country', how = 'right', rsuffix= month)
  return country_ratings_per_month




def rename_country_columns(country_df):
  # Make months dictionary to keep track of which months were used
  for name in country_df.columns:
    for id, month in months.items():
      if month[0] in name:
        country_df = country_df.rename(columns = {name: month[0]})
        months[id].append("used")
  leftover_name = [(id, month) for (id, month) in months.items() if "used" not in month]
  leftover_name = leftover_name [0][1]
  country_df = country_df.rename(columns = {"Average Rating": leftover_name[0]})
  return country_df



country_ratings_per_month = opening_country_ratings()
country_ratings_per_month = rename_country_columns(country_ratings_per_month)
country_ratings_per_month.head()

Country  October  November    August  September      July      June  \
10      AR     4.20  4.200000  4.200000       4.20  4.200000  4.200000   
14      AT     3.83  3.830000  3.830000       3.83  3.830000  3.859333   
13      AU     4.20  4.191333  4.199677       4.20  4.193871  4.190000   
28      BA     5.00  5.000000  5.000000       5.00  5.000000  5.000000   
18      BD     5.00  5.000000  5.000000       5.00  5.000000  5.000000   

    December  
10      4.20  
14      3.83  
13      4.18  
28      5.00  
18      5.00

In [ ]:
# INITIALISING SHAPE FILE
shapefile = "ne_110m_admin_0_countries.shp"
map = gpd.read_file (shapefile)[['ADMIN','ADM0_A3', 'geometry']]
map.columns = ['country', 'country code', 'geometry']
map.head()

country country code  \
0                         Fiji          FJI   
1  United Republic of Tanzania          TZA   
2               Western Sahara          SAH   
3                       Canada          CAN   
4     United States of America          USA   

                                            geometry  
0  MULTIPOLYGON (((180.00000 -16.06713, 180.00000...  
1  POLYGON ((33.90371 -0.95000, 34.07262 -1.05982...  
2  POLYGON ((-8.66559 27.65643, -8.66512 27.58948...  
3  MULTIPOLYGON (((-122.84000 49.00000, -122.9742...  
4  MULTIPOLYGON (((-122.84000 49.00000, -120.0000...

In [ ]:
# CREATING COMMON INDEX BETWEEN RATINGS AND SHAPEFILE

'''
  The shapefile is indexed by a three-letter country code, whereas the ratings
  are indexed by a two-letter country code. Thus, downloaded a country code .csv
  file from: https://github.com/rmosolgo/countrysaurus/blob/master/public/data/country_codes.csv
  to re-index the shapefile
'''
country_codes = pd.read_csv('country_codes.csv')
country_codes = country_codes[["alpha-2", "name", "alpha-3", "region"]]
map_with_country_codes = map.merge(country_codes, left_on = 'country code', right_on = "alpha-3", how = "left")
map_with_country_codes.head()

country country code  \
0                         Fiji          FJI   
1  United Republic of Tanzania          TZA   
2               Western Sahara          SAH   
3                       Canada          CAN   
4     United States of America          USA   

                                            geometry alpha-2  \
0  MULTIPOLYGON (((180.00000 -16.06713, 180.00000...      FJ   
1  POLYGON ((33.90371 -0.95000, 34.07262 -1.05982...      TZ   
2  POLYGON ((-8.66559 27.65643, -8.66512 27.58948...     NaN   
3  MULTIPOLYGON (((-122.84000 49.00000, -122.9742...      CA   
4  MULTIPOLYGON (((-122.84000 49.00000, -120.0000...      US   

                           name alpha-3    region  
0                          Fiji     FJI   Oceania  
1  Tanzania, United Republic of     TZA    Africa  
2                           NaN     NaN       NaN  
3                        Canada     CAN  Americas  
4      United States of America     USA  Americas

In [ ]:
# CREATING SHAPEFILE FOR RATINGS
choropleth_ratings = map_with_country_codes.merge(country_ratings_per_month, left_on = 'alpha-2', right_on = 'Country', how = 'left')
choropleth_ratings.head()



country country code  \
0                         Fiji          FJI   
1  United Republic of Tanzania          TZA   
2               Western Sahara          SAH   
3                       Canada          CAN   
4     United States of America          USA   

                                            geometry alpha-2  \
0  MULTIPOLYGON (((180.00000 -16.06713, 180.00000...      FJ   
1  POLYGON ((33.90371 -0.95000, 34.07262 -1.05982...      TZ   
2  POLYGON ((-8.66559 27.65643, -8.66512 27.58948...     NaN   
3  MULTIPOLYGON (((-122.84000 49.00000, -122.9742...      CA   
4  MULTIPOLYGON (((-122.84000 49.00000, -120.0000...      US   

                           name alpha-3    region Country  October  November  \
0                          Fiji     FJI   Oceania     NaN      NaN       NaN   
1  Tanzania, United Republic of     TZA    Africa     NaN      NaN       NaN   
2                           NaN     NaN       NaN     NaN      NaN       NaN   
3                        Canada     CAN  Americas      CA     4.13  4.120667   
4      United States of America     USA  Americas      US     4.03  4.030000   

     August  September      July  June  December  
0       NaN        NaN       NaN   NaN       NaN  
1       NaN        NaN       NaN   NaN       NaN  
2       NaN        NaN       NaN   NaN       NaN  
3  4.130000       4.13  4.120645  4.12  4.119677  
4  4.033871       4.03  4.040000  4.04  4.030323

In [ ]:
# CALCULATING SALES VOLUME PER DAY/PER MONTH PER COUNTRY && CREATING SHAPEFILE FOR SALES VOLUME PER COUNTRY ON CHOROPLETH


## PER DAY ##
sales_by_country_per_day = sales[sales['Transaction Date'].notna()].loc[:,['Transaction Date','Amount (Merchant Currency)', 'Buyer Country']]
sales_by_country_per_day['Transaction Date'] = pd.to_datetime(sales_by_country_per_day['Transaction Date']) # Note: if this cell doesn't run please try adding format = 'mixed' as an argument to pd.datetime()
sorted_sales_by_country_per_day = sales_by_country_per_day.sort_values(by = "Transaction Date")


# Cumulative sales per country
grouped_sales_by_country_per_day = sales_by_country_per_day.groupby(['Transaction Date', 'Buyer Country'])['Amount (Merchant Currency)'].sum().reset_index()
all_dates = pd.date_range(grouped_sales_by_country_per_day['Transaction Date'].min(), grouped_sales_by_country_per_day['Transaction Date'].max(), freq='D')
all_countries = grouped_sales_by_country_per_day['Buyer Country'].unique()
multi_index = pd.MultiIndex.from_product([all_dates, all_countries], names=['Transaction Date', 'Buyer Country'])
grouped_sales_by_country_per_day = grouped_sales_by_country_per_day.set_index(['Transaction Date', 'Buyer Country']).reindex(multi_index, fill_value=0).reset_index()
grouped_sales_by_country_per_day['Cumulative Sales'] = grouped_sales_by_country_per_day.groupby(['Buyer Country'])['Amount (Merchant Currency)'].cumsum()

cumulative_sales_volume_per_country_p = pd.pivot_table(grouped_sales_by_country_per_day, values = "Cumulative Sales", index = "Buyer Country", columns = "Transaction Date")
cumulative_sales_per_day_choropleth = map_with_country_codes.merge(cumulative_sales_volume_per_country_p, left_on = 'alpha-2', right_on = 'Buyer Country', how = 'left')
cumulative_sales_per_day_choropleth = cumulative_sales_per_day_choropleth.fillna(0)


## PER MONTH ##
temp_by_country_per_day = sales_by_country_per_day.copy(deep = True)
temp_by_country_per_day['Transaction Date'] = pd.to_datetime(temp_by_country_per_day['Transaction Date']) # Note: if this cell doesn't run please try adding format = 'mixed' as an argument to pd.datetime()
grouper = pd.Grouper(freq="1M")
sales_by_country_per_day_dateindex = temp_by_country_per_day.set_index("Transaction Date")

month_purchases_per_country = sales_by_country_per_day_dateindex.groupby([grouper, "Buyer Country"]).count()
month_turnover_per_country = sales_by_country_per_day_dateindex.groupby([grouper, "Buyer Country"]).sum()

In [ ]:
# CALCULATING CUMULATIVE TRANSACTION COUNTS PER COUNTRY

grouped_transactions_by_country = sales_by_country_per_day.groupby(['Transaction Date', 'Buyer Country'])['Buyer Country'].count().reset_index(name="Transaction Count")
all_dates = pd.date_range(grouped_sales_by_country_per_day['Transaction Date'].min(), grouped_sales_by_country_per_day['Transaction Date'].max(), freq='D')
all_countries = grouped_sales_by_country_per_day['Buyer Country'].unique()
multi_index = pd.MultiIndex.from_product([all_dates, all_countries], names=['Transaction Date', 'Buyer Country'])
grouped_transactions_by_country_per_day = grouped_transactions_by_country.set_index(['Transaction Date', 'Buyer Country']).reindex(multi_index, fill_value=0).reset_index()
grouped_transactions_by_country_per_day['Cumulative Transactions'] = grouped_transactions_by_country_per_day.groupby(['Buyer Country'])['Transaction Count'].cumsum()

cumulative_transactions_per_country_p = pd.pivot_table(grouped_transactions_by_country_per_day, values = "Cumulative Transactions", index = "Buyer Country", columns = "Transaction Date")
cumulative_transactions_per_country_p_sorted = cumulative_transactions_per_country_p.sort_values(by = "2021-12-31", ascending = False)
cumulative_transactions_per_country_p_sorted

Transaction Date  2021-06-01  2021-06-02  2021-06-03  2021-06-04  2021-06-05  \
Buyer Country                                                                  
US                         2           9          15          21          23   
GB                         0           1           1           1           1   
CA                         0           0           0           0           0   
DE                         0           0           0           0           0   
NL                         0           0           0           1           1   
AU                         0           0           0           0           0   
IT                         0           0           0           0           0   
SE                         0           1           1           1           1   
MX                         0           0           0           0           0   
GR                         0           0           0           0           0   
BR                         0           0           0           0           0   
RU                         0           0           0           0           0   
CZ                         0           0           0           0           0   
PL                         0           0           0           0           0   
DK                         0           0           0           0           0   
UA                         0           0           0           0           0   
BE                         0           0           0           0           0   
PT                         0           0           0           0           0   
ES                         0           0           0           0           0   
PH                         0           0           0           0           0   
AT                         0           0           0           0           0   
FR                         0           0           0           0           0   
CH                         0           0           0           0           0   
PR                         0           0           0           0           0   
NZ                         0           0           0           0           0   
TR                         0           0           0           0           0   
IE                         0           0           0           0           0   
ZA                         0           0           0           0           0   
MY                         0           0           0           0           0   
LT                         0           0           0           0           0   
ID                         0           0           0           0           0   
CR                         0           0           0           0           0   
CO                         0           0           0           0           0   
NO                         0           0           0           0           0   
IL                         0           1           1           1           1   
FI                         0           0           0           0           0   
BG                         0           0           0           0           0   
AR                         0           0           0           0           0   

Transaction Date  2021-06-06  2021-06-07  2021-06-08  2021-06-09  2021-06-10  \
Buyer Country                                                                  
US                        36          48          50          54          55   
GB                         1           1           2           2           2   
CA                         0           0           0           0           0   
DE                         0           0           0           0           0   
NL                         1           1           1           1           1   
AU                         0           1           1           1           1   
IT                         0           0           0           0           0   
SE                         1           1           1           1           1   

#cumulative transactions

In [ ]:
## CUMULATIVE TRANSACTION COUNT PER DAY PLOT TO IDENTIFY EMERGING COUNTRIES
emerging_markets = pd.pivot_table(grouped_transactions_by_country_per_day, values = "Cumulative Transactions", index = "Transaction Date", columns = "Buyer Country")
print(emerging_markets.head())
emerging_markets = emerging_markets.loc[:,["GB", "CA", "DE", "NL", "AU", "IT"]]

emerging_markets_cds = ColumnDataSource(emerging_markets)



output_notebook()
tools = "pan,wheel_zoom,box_zoom,reset"
tooltips_GB = [('Cumulative Transaction Count','@{GB}'), ('Date', '@{Transaction Date}{%F}')]
tooltips_CA = [('Cumulative Transaction Count','@{CA}'), ('Date', '@{Transaction Date}{%F}')]
tooltips_DE = [('Cumulative Transaction Count','@{DE}'), ('Date', '@{Transaction Date}{%F}')]
tooltips_NL = [('Cumulative Transaction Count','@{NL}'), ('Date', '@{Transaction Date}{%F}')]
tooltips_AU = [('Cumulative Transaction Count','@{AU}'), ('Date', '@{Transaction Date}{%F}')]
tooltips_IT = [('Cumulative Transaction Count','@{IT}'), ('Date', '@{Transaction Date}{%F}')]



cumulative_downloads = figure(title = "Cumulative Downloads to Date (Emerging Markets)", x_axis_label="Day", y_axis_label="Number of Downloads to Date", height=figure_height, width=figure_width, x_axis_type = 'datetime', tools=tools)
GB_line = cumulative_downloads.line(source=emerging_markets_cds, x = 'Transaction Date', y='GB',color=palette[0],legend_label='UK')
CA_line = cumulative_downloads.line(source=emerging_markets_cds, x = 'Transaction Date', y='CA',color=palette[1],legend_label='Canada')
DE_line = cumulative_downloads.line(source=emerging_markets_cds, x = 'Transaction Date', y='DE',color=palette[2],legend_label='Germany')
NL_line = cumulative_downloads.line(source=emerging_markets_cds, x = 'Transaction Date', y='NL',color=palette[3],legend_label='The Netherlands')
AU_line = cumulative_downloads.line(source=emerging_markets_cds, x = 'Transaction Date', y='AU',color=palette[4],legend_label='Australia')
IT_line = cumulative_downloads.line(source=emerging_markets_cds, x = 'Transaction Date', y='IT',color=palette[5],legend_label='Italy')


cumulative_downloads.yaxis.axis_label = "Cumulative Downloads to Date"
cumulative_downloads.yaxis.axis_label_text_color = palette[6]



cumulative_downloads.add_tools(HoverTool(tooltips=tooltips_GB, renderers=[GB_line], formatters={"@{Transaction Date}":"datetime"}))
cumulative_downloads.add_tools(HoverTool(tooltips=tooltips_CA, renderers=[CA_line], formatters={"@{Transaction Date}":"datetime"}))
cumulative_downloads.add_tools(HoverTool(tooltips=tooltips_DE, renderers=[DE_line], formatters={"@{Transaction Date}":"datetime"}))
cumulative_downloads.add_tools(HoverTool(tooltips=tooltips_NL, renderers=[NL_line], formatters={"@{Transaction Date}":"datetime"}))
cumulative_downloads.add_tools(HoverTool(tooltips=tooltips_AU, renderers=[AU_line], formatters={"@{Transaction Date}":"datetime"}))
cumulative_downloads.add_tools(HoverTool(tooltips=tooltips_IT, renderers=[IT_line], formatters={"@{Transaction Date}":"datetime"}))

cumulative_downloads.legend.click_policy = 'mute'
cumulative_downloads.legend.location = 'top_left'

show(cumulative_downloads)


Buyer Country     AR  AT  AU  BE  BG  BR  CA  CH  CO  CR  ...  PH  PL  PR  PT  \
Transaction Date                                          ...                   
2021-06-01         0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   
2021-06-02         0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   
2021-06-03         0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   
2021-06-04         0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   
2021-06-05         0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   

Buyer Country     RU  SE  TR  UA  US  ZA  
Transaction Date                          
2021-06-01         0   0   0   0   2   0  
2021-06-02         0   1   0   0   9   0  
2021-06-03         0   1   0   0  15   0  
2021-06-04         0   1   0   0  21   0  
2021-06-05         0   1   0   0  23   0  

[5 rows x 38 columns]


In [ ]:
## CUMULATIVE TRANSACTION COUNT PER DAY PLOT (HIGHEST VOLUME)
highest_volume = pd.pivot_table(grouped_transactions_by_country_per_day, values = "Cumulative Transactions", index = "Transaction Date", columns = "Buyer Country")
highest_volume = highest_volume.loc[:,["GB", "CA", "DE", "NL", "AU", "IT", "US"]]

highest_volume_cds = ColumnDataSource(highest_volume)

palette=brewer['Dark2'][8][::-1]


output_notebook()
tools = "pan,wheel_zoom,box_zoom,reset"
tooltips_GB = [('Cumulative Transaction Count','@{GB}'), ('Date', '@{Transaction Date}{%F}')]
tooltips_CA = [('Cumulative Transaction Count','@{CA}'), ('Date', '@{Transaction Date}{%F}')]
tooltips_DE = [('Cumulative Transaction Count','@{DE}'), ('Date', '@{Transaction Date}{%F}')]
tooltips_NL = [('Cumulative Transaction Count','@{NL}'), ('Date', '@{Transaction Date}{%F}')]
tooltips_AU = [('Cumulative Transaction Count','@{AU}'), ('Date', '@{Transaction Date}{%F}')]
tooltips_IT = [('Cumulative Transaction Count','@{IT}'), ('Date', '@{Transaction Date}{%F}')]
tooltips_US = [('Cumulative Transaction Count','@{US}'), ('Date', '@{Transaction Date}{%F}')]



highest_volume = figure(title = "Cumulative Downloads to Date (High Volume Countries)", x_axis_label="Day", y_axis_label="Number of Downloads to Date", height=figure_height, width=figure_width, x_axis_type = 'datetime', tools=tools)
GB_line = highest_volume.line(source=highest_volume_cds, x = 'Transaction Date', y='GB',color=palette[0],legend_label='UK')
CA_line = highest_volume.line(source=highest_volume_cds, x = 'Transaction Date', y='CA',color=palette[1],legend_label='Canada')
DE_line = highest_volume.line(source=highest_volume_cds, x = 'Transaction Date', y='DE',color=palette[2],legend_label='Germany')
NL_line = highest_volume.line(source=highest_volume_cds, x = 'Transaction Date', y='NL',color=palette[3],legend_label='The Netherlands')
AU_line = highest_volume.line(source=highest_volume_cds, x = 'Transaction Date', y='AU',color=palette[4],legend_label='Australia')
IT_line = highest_volume.line(source=highest_volume_cds, x = 'Transaction Date', y='IT',color=palette[5],legend_label='Italy')
US_line = highest_volume.line(source=highest_volume_cds, x = 'Transaction Date', y='US',color=palette[6],legend_label='United States')


highest_volume.yaxis.axis_label = "Cumulative Downloads to Date"
highest_volume.yaxis.axis_label_text_color = palette[7]



highest_volume.add_tools(HoverTool(tooltips=tooltips_GB, renderers=[GB_line], formatters={"@{Transaction Date}":"datetime"}))
highest_volume.add_tools(HoverTool(tooltips=tooltips_CA, renderers=[CA_line], formatters={"@{Transaction Date}":"datetime"}))
highest_volume.add_tools(HoverTool(tooltips=tooltips_DE, renderers=[DE_line], formatters={"@{Transaction Date}":"datetime"}))
highest_volume.add_tools(HoverTool(tooltips=tooltips_NL, renderers=[NL_line], formatters={"@{Transaction Date}":"datetime"}))
highest_volume.add_tools(HoverTool(tooltips=tooltips_AU, renderers=[AU_line], formatters={"@{Transaction Date}":"datetime"}))
highest_volume.add_tools(HoverTool(tooltips=tooltips_IT, renderers=[IT_line], formatters={"@{Transaction Date}":"datetime"}))
highest_volume.add_tools(HoverTool(tooltips=tooltips_US, renderers=[US_line], formatters={"@{Transaction Date}":"datetime"}))



highest_volume.legend.click_policy = 'mute'
highest_volume.legend.location = 'top_left'

show(highest_volume)


In [ ]:
emerg_panel = TabPanel(child = cumulative_downloads, title='Emerging Markets')
highvol_panel = TabPanel(child=highest_volume, title='High Vol Countries')


sales_tabs = Tabs(tabs = [emerg_panel, highvol_panel,sales_vol_panel])

In [ ]:
## Average Country Rating

average_country_rating = country_ratings_per_month[['Country']].copy()

average_country_rating['Average Rating'] = country_ratings_per_month.drop('Country', axis=1).mean(axis=1)

average_country_rating_cloropleth = map_with_country_codes.merge(average_country_rating, left_on = 'alpha-2', right_on = 'Country', how = 'left')
average_country_rating_cloropleth



country country code  \
0                           Fiji          FJI   
1    United Republic of Tanzania          TZA   
2                 Western Sahara          SAH   
3                         Canada          CAN   
4       United States of America          USA   
..                           ...          ...   
172           Republic of Serbia          SRB   
173                   Montenegro          MNE   
174                       Kosovo          KOS   
175          Trinidad and Tobago          TTO   
176                  South Sudan          SDS   

                                              geometry alpha-2  \
0    MULTIPOLYGON (((180.00000 -16.06713, 180.00000...      FJ   
1    POLYGON ((33.90371 -0.95000, 34.07262 -1.05982...      TZ   
2    POLYGON ((-8.66559 27.65643, -8.66512 27.58948...     NaN   
3    MULTIPOLYGON (((-122.84000 49.00000, -122.9742...      CA   
4    MULTIPOLYGON (((-122.84000 49.00000, -120.0000...      US   
..                                                 ...     ...   
172  POLYGON ((18.82982 45.90887, 18.82984 45.90888...      RS   
173  POLYGON ((20.07070 42.58863, 19.80161 42.50009...      ME   
174  POLYGON ((20.59025 41.85541, 20.52295 42.21787...     NaN   
175  POLYGON ((-61.68000 10.76000, -61.10500 10.890...      TT   
176  POLYGON ((30.83385 3.50917, 29.95350 4.17370, ...     NaN   

                             name alpha-3    region Country  Average Rating  
0                            Fiji     FJI   Oceania     NaN             NaN  
1    Tanzania, United Republic of     TZA    Africa     NaN             NaN  
2                             NaN     NaN       NaN     NaN             NaN  
3                          Canada     CAN  Americas      CA        4.124427  
4        United States of America     USA  Americas      US        4.033456  
..                            ...     ...       ...     ...             ...  
172                        Serbia     SRB    Europe      RS        4.629724  
173                    Montenegro     MNE    Europe     NaN             NaN  
174                           NaN     NaN       NaN     NaN             NaN  
175           Trinidad and Tobago     TTO  Americas     NaN             NaN  
176                           NaN     NaN       NaN     NaN             NaN  

[177 rows x 9 columns]

In [ ]:
## MAKING CHOROPLETH FOR AVERAGE COUNTRY RATING (HISTORICAL)
average_country_rating = country_ratings_per_month[['Country']].copy()
average_country_rating['Average Rating'] = country_ratings_per_month.drop('Country', axis=1).mean(axis=1)
average_country_rating_cloropleth = map_with_country_codes.merge(average_country_rating, left_on = 'alpha-2', right_on = 'Country', how = 'left')

In [ ]:
## MAKING CHOROPLETH FOR AVERAGE COUNTRY RATING (NEW/DAILY)
recent_daily_ratings= per_country[per_country["Daily Average Rating"].notna()]
recent_daily_ratings = recent_daily_ratings.loc[:,["Country", "Date", "Daily Average Rating"]].groupby("Country").mean(numeric_only = True)
recent_daily_ratings_choropleth = map_with_country_codes.merge(recent_daily_ratings, left_on = 'alpha-2', right_on = 'Country', how = 'left')
recent_daily_ratings


Daily Average Rating
Country                      
AR                   4.000000
AT                   3.000000
AU                   4.000000
BR                   3.000000
CA                   3.750000
CO                   5.000000
DE                   5.000000
ES                   5.000000
FR                   2.333333
GB                   3.400000
GR                   4.000000
ID                   5.000000
IR                   5.000000
PH                   4.000000
RU                   4.000000
SK                   5.000000
TR                   5.000000
US                   3.577778

In [ ]:
# PLOTTING MONTHLY MEASURES WITH BOKEH

# Function to sanity-check average ratings (they are almost constant)
def calculate_differences():
  differences = choropleth_ratings[["June", "July", "August", "September", "October", "November", "December"]].diff(axis = 1)
  differences.dropna(how = 'all', inplace = True)
  return differences


def rename_column_names_from_timestamp_to_str(df):
  timestamp_to_str = dict()
  for maybe_date in list(df.columns):
    if type(maybe_date) == pd._libs.tslibs.timestamps.Timestamp:
      timestamp_to_str[maybe_date] = maybe_date.strftime("%D")

  df.rename(columns = timestamp_to_str, inplace=True)

# Iterate through df.columns, return list of names of columns that are probably dates.
# Note: this assumes the date columns are already sorted
def get_date_columns(df):
    date_columns = []
    for column_name in df.columns:
        try:
            pd.to_datetime(df[column_name])
            date_columns.append(column_name)
        except:
            pass
    return date_columns

def get_geodatasource(gdf):
  json_data = json.dumps(json.loads(gdf.to_json()))
  return GeoJSONDataSource(geojson = json_data)

def plot_base_bokeh_map(df, chart_name, column_name, palette, color_mapper_range=None):
  geosource = get_geodatasource(df)
  date_values = get_date_columns(df)

  values = df[column_name]

  low_value_for_mapper = color_mapper_range[0] if color_mapper_range is not None else values.min()
  high_value_for_mapper = color_mapper_range[1] if color_mapper_range is not None else values.max()

  color_mapper = LinearColorMapper(palette = palette, low = low_value_for_mapper, high = high_value_for_mapper)
  color_bar = ColorBar(color_mapper=color_mapper)
  tools = "wheel_zoom, pan, reset"

  fill_color = {'field' : column_name, 'transform': color_mapper}

  p = figure(title = chart_name, height = figure_height, width = figure_width, tools = tools)
  patches = p.patches('xs','ys', source=geosource, fill_alpha=1, line_width=0.5, line_color='black',
              fill_color=fill_color)
  p.add_layout(color_bar, 'below')
  p.xaxis.visible = False
  p.yaxis.visible = False

  return p, color_mapper, patches

def plot_bokeh_map_static(df, chart_name, column_name, palette, color_mapper_range=None):
  p, color_mapper, patches = plot_base_bokeh_map(df, chart_name, column_name, palette, color_mapper_range)

  hvr=HoverTool(tooltips=[
    ("Country", "@{alpha-3}"),
    ("Value", "@{" + column_name + "}{0.000}"), # {0.000} is the formatting for the value (3 decimal places)
  ])

  p.add_tools(hvr)
  return bokeh_column(p)

def plot_bokeh_map_by_month(df, chart_name, palette, color_mapper_range, months):
  geosource = get_geodatasource(df)
  date_values = get_date_columns(df)
  column_name = months[0]

  p, color_mapper, patches = plot_base_bokeh_map(df, chart_name, column_name, palette, color_mapper_range=color_mapper_range)

  hvr=HoverTool(tooltips=[
    ("Country", "@{alpha-3}"),
    ("Value", "@{" + column_name + "}{0.000}"), # {0.000} is the formatting for the value (3 decimal places)
  ])

  months_slider = Slider(start=0, end=len(months) -1, value=0, step=1, sizing_mode="stretch_width", format=CustomJSTickFormatter(args=dict(months=months), code="return months[Math.round(tick)]"))
  callback = CustomJS(args=dict(hvr=hvr, months=months, patches=patches, color_mapper=color_mapper), code="""
        const month = months[cb_obj.value];

        // learned/based on https://discourse.bokeh.org/t/update-tooltips-with-customjs-callback-function/9907
        hvr.tooltips[1][1]=`@{${month}}{0.000}`;
        hvr.properties.tooltips.change.emit();

        patches.glyph.fill_color = {'field': month, 'transform': color_mapper};
        patches.change.emit();
""")

  p.add_tools(hvr)

  months_slider.js_on_change('value', callback)

  return bokeh_column(p, months_slider)


def plot_bokeh_map_by_day(df, chart_name, palette, color_mapper_range=None):
  date_values = get_date_columns(df)

  column_name = date_values[0]

  start_date = datetime.strptime(date_values[0],"%m/%d/%y")
  end_date = datetime.strptime(date_values[-1],"%m/%d/%y")

  p, color_mapper, patches = plot_base_bokeh_map(df, chart_name, column_name, palette, color_mapper_range=(color_mapper_range if color_mapper_range is not None else (0, df[date_values[-1]].max())))

  hvr=HoverTool(tooltips=[
    ("Country", "@{alpha-3}"),
    ("Value", "@{" + column_name + "}{0.000}"), # {0.000} is the formatting for the value (3 decimal places)
  ])

  p.add_tools(hvr)

  date_slider = DateSlider(start=start_date, end=end_date, value=start_date, step=1, title='Date', sizing_mode="stretch_width")

  callback = CustomJS(args=dict(hvr=hvr, patches=patches, color_mapper=color_mapper), code="""
        const date = new Date(cb_obj.value); // the date_slider value is epoch time/timestamp so needs to be converted

        const day = date.getDate().toString().padStart(2, '0');
        const month = (date.getMonth() + 1).toString().padStart(2, '0');
        const year = date.getFullYear().toString().slice(-2);

        const formattedDate = `${month}/${day}/${year}`; // formattedDate corresponds to the column in df

        // learned/based on https://discourse.bokeh.org/t/update-tooltips-with-customjs-callback-function/9907
        hvr.tooltips[1][1]=`@{${formattedDate}}{0}`;
        hvr.properties.tooltips.change.emit();

        patches.glyph.fill_color = {'field': formattedDate, 'transform': color_mapper};
        patches.change.emit();
""")

  date_slider.js_on_change('value', callback)


  return bokeh_column(p, Div(text='''<p style="font-weight: bold"> Please Note: due to the Sales Revenue for the US being so high, we docked the value for the graph to 500.
   <br> The actual value is viewable by hovering over each country.</p>'''), date_slider)

rename_column_names_from_timestamp_to_str(cumulative_sales_per_day_choropleth)


## Plotting the maps
cumulative_sales_revenue_map = plot_bokeh_map_by_day(cumulative_sales_per_day_choropleth, "Cumulative Sales Revenue by Date", color_mapper_range=(0, 500), palette=cc.CET_L12)
country_ratings_per_month = plot_bokeh_map_by_month(choropleth_ratings, "Average Country Ratings Per Month", palette=brewer['BuGn'][5][::-1], months=["June", "July", "August", "September", "October", "November", "December"], color_mapper_range=(0, 5))
average_country_ratings_static = plot_bokeh_map_static(average_country_rating_cloropleth, "Historic Average Rating by Country", "Average Rating", palette=brewer['BuGn'][5][::-1], color_mapper_range=(0, 5))
recent_ratings_per_country_static = plot_bokeh_map_static(recent_daily_ratings_choropleth, "Recent Average Rating by Country", "Daily Average Rating", palette = brewer['BuGn'][5][::-1], color_mapper_range=(0, 5))


show(cumulative_sales_revenue_map)
show(country_ratings_per_month)
show(average_country_ratings_static)
show(recent_ratings_per_country_static)
## Can also print it out in a single HTML page:
# output_file('all-plots.html')

# all_plots = bokeh_column(
#     plot_bokeh_map_by_day(cumulative_sales_per_day_choropleth, "Cumulative Sales Revenue per Day"),
#     plot_bokeh_map_by_day(cumulative_transaction_count_per_day_choropleth, "Cumulative Transaction Count per Day"),
#     plot_bokeh_map_by_month(choropleth_ratings, "Country Ratings Per Month", ["June", "July", "August", "September", "October", "November", "December"], 0, 5)
# )

# show(all_plots)


In [ ]:
# ALL FOUR MAPS
revenue_panel = TabPanel(child = cumulative_sales_revenue_map, title = "Cumulative Sales Revenue")
monthly_ratings_panel = TabPanel(child=country_ratings_per_month, title = "Average Rating per Month")
total_ratings_panel = TabPanel(child=average_country_ratings_static, title = "Historical Average Ratings")
recent_ratings_panel  = TabPanel(child = recent_ratings_per_country_static, title ="Recent Average Ratings")

# Assign the panels to Tabs
map_tabs = Tabs(tabs=[revenue_panel, total_ratings_panel, monthly_ratings_panel, recent_ratings_panel])

# Show the tabbed layout
show(map_tabs)

#**SEGMENTATION**

In [ ]:
#  SALES PER SKU-ID DATA PROCESSING
sales_p_skuid = sales[sales['Transaction Date'].notna()].loc[:,['Amount (Merchant Currency)','Sku Id']]
amount_p_skuid = sales_p_skuid.groupby('Sku Id').sum()
count_p_skuid = sales_p_skuid.groupby('Sku Id').count()


amount_p_skuid = ColumnDataSource(amount_p_skuid)
count_p_skuid = ColumnDataSource(count_p_skuid)



In [ ]:
# SALES PER SKU-ID PLOTTING

tools = "wheel_zoom,box_zoom,pan,reset"
tooltips_amount = [('Amount (EUR)','@{Amount (Merchant Currency)}{0.00 a}')]
tooltips_count = [('Count','@{Amount (Merchant Currency)}')]

skuid_sales_fig = figure(height = figure_height, width = figure_width,x_range = amount_p_skuid.data['Sku Id'], title = "Sales per Sku Id", x_axis_label="Sku Id", y_axis_label="Amount (EUR)", tools=tools)

skuid_sales_fig.extra_y_ranges['count'] = DataRange1d(bounds = (0,count_p_skuid.data['Amount (Merchant Currency)'].max()*2))
skuid_sales_fig.extra_y_ranges['amount'] = DataRange1d(bounds = (0,amount_p_skuid.data['Amount (Merchant Currency)'].max()*1.1))

skuid_amount_fig = skuid_sales_fig.vbar(width = 0.9, y_range_name = 'amount', source=amount_p_skuid, x = 'Sku Id', top='Amount (Merchant Currency)',color=palette[2],legend_label='Revenue (in EUR)')
skuid_count_fig = skuid_sales_fig.vbar(width = 0.9, y_range_name = 'count', source=count_p_skuid, x = 'Sku Id', top='Amount (Merchant Currency)', color=palette[7],legend_label='Units Sold')

skuid_sales_fig.yaxis.axis_label = "Revenue"
skuid_sales_fig.yaxis.axis_label_text_color = palette[2]
count_axis = LinearAxis(y_range_name="count",axis_label_text_color = palette[7],axis_label = "Units Sold")
skuid_sales_fig.add_layout(count_axis,"left")

skuid_sales_fig.xaxis.axis_label = "Product"
skuid_sales_fig.xaxis.major_label_orientation = 3.14/16

skuid_sales_fig.add_tools(HoverTool(tooltips=tooltips_count, renderers=[skuid_count_fig]))
skuid_sales_fig.add_tools(HoverTool(tooltips=tooltips_amount, renderers=[skuid_amount_fig]))

skuid_sales_fig.legend.click_policy = 'hide'
skuid_sales_fig.legend.location='top_left'

In [ ]:
# SEGMENTATION BY PRODUCT TITLE
sales_by_product_title = sales[sales['Transaction Date'].notna()].loc[:,['Transaction Date','Product Title']]
sales_by_product_indexed = sales_by_product_title.groupby("Product Title").count()
sales_by_product_indexed = sales_by_product_indexed.rename(columns = {"Transaction Date":"Count of Product Sold"})
sales_by_product_temp = sales_by_product_indexed.reset_index()
sales_by_product_temp = sales_by_product_temp.sort_values(by = "Product Title")


revenue_by_product_title = sales[sales['Transaction Date'].notna()].loc[:,['Product Title', 'Amount (Merchant Currency)']]
revenue_by_product_indexed = revenue_by_product_title.groupby("Product Title").sum()
revenue_by_product_indexed = revenue_by_product_indexed.rename(columns = {"Amount (Merchant Currency)":"Revenue"})
revenue_by_product_temp = revenue_by_product_indexed.reset_index()
revenue_by_product_temp = revenue_by_product_temp.sort_values(by = "Product Title")

sales_by_product_temp


Product Title  Count of Product Sold
0  Character Manager (Complete Reference for DnD 5)                    996
1           DM Tools (Complete Reference for DnD 5)                    710

In [ ]:
# SALES PER PRODUCT PLOTTING
revenue_by_product = ColumnDataSource(revenue_by_product_temp)
count_by_product = ColumnDataSource(sales_by_product_temp)
print(type(revenue_by_product.data["Product Title"]))


output_notebook()


tools = "wheel_zoom,box_zoom,pan,reset"
tooltips_product_count = [('Amount of Product Sold','@{Count of Product Sold}')]
tooltips_revenue = [('Revenue', '@{Revenue}')]

product_sales_fig = figure(x_range = np.flip(revenue_by_product.data["Product Title"]), title = "Sales per Product Title", x_axis_label = "Product Title", y_axis_label = "Revenue (EUR)", height = figure_height,width = figure_width,tools=tools)


revenue_bars = product_sales_fig.vbar(width = 0.9, source=revenue_by_product, x = 'Product Title', top='Revenue',color=palette[2],legend_label='Revenue (in EUR)')
count_bars = product_sales_fig.vbar(width = 0.9, source=count_by_product, x = 'Product Title', top='Count of Product Sold',color=palette[7],legend_label='Units Sold')

product_sales_fig.extra_y_ranges['Count of Product Sold'] = DataRange1d(renderers = [count_bars])

product_sales_fig.yaxis.axis_label = "Revenue"
product_sales_fig.yaxis.axis_label_text_color = palette[2]
counts_axis = LinearAxis(y_range_name="Count of Product Sold",axis_label_text_color = palette[7],axis_label = "Units Sold")
product_sales_fig.add_layout(counts_axis,"left")

product_sales_fig.xaxis.axis_label = "Product"
product_sales_fig.xaxis.major_label_orientation = 3.14/16

product_sales_fig.add_tools(HoverTool(tooltips=tooltips_product_count, renderers=[count_bars]))
product_sales_fig.add_tools(HoverTool(tooltips=tooltips_revenue, renderers=[revenue_bars]))

product_sales_fig.legend.click_policy = 'hide'
product_sales_fig.legend.location='top_left'

show(product_sales_fig)



<class 'numpy.ndarray'>


In [ ]:
# SEGMENTATION BY COUNTRY OF SALE
revenue_by_country = sales_by_country_per_day.groupby(['Buyer Country']).sum(numeric_only = True)
units_by_country = sales_by_country_per_day.groupby(['Buyer Country']).count()

units_by_country = units_by_country.loc[:,['Amount (Merchant Currency)']]
units_by_country_temp = units_by_country.rename(columns = {"Amount (Merchant Currency)":"Units Sold"})


In [ ]:
# SEGMENTATION BY COUNTRY PLOTTING

revenue_by_country_cds = ColumnDataSource(revenue_by_country)
units_by_country_cds= ColumnDataSource(units_by_country_temp)

tools = "wheel_zoom,box_zoom,pan,reset"
tooltips_product_count = [('Units of Product Sold','@{Units Sold}')]
tooltips_revenue = [('Revenue', '@{Amount (Merchant Currency)}')]

country_sales_fig = figure(x_range = revenue_by_country_cds.data["Buyer Country"], title = "Sales per Country", x_axis_label = "Buyer Country", y_axis_label = "Revenue (EUR)", height = figure_height, width = 1200 ,tools=tools)

revenue_by_country_bars = country_sales_fig.vbar(width = 0.9, source=revenue_by_country_cds, x = 'Buyer Country', top='Amount (Merchant Currency)',color=palette[2],legend_label='Revenue (in EUR)')
units_by_country_bars = country_sales_fig.vbar(width = 0.9, source=units_by_country_cds, x = 'Buyer Country', top='Units Sold',color=palette[7],legend_label='Units Sold')

country_sales_fig.extra_y_ranges['Units Sold'] = DataRange1d(renderers = [units_by_country_bars])

country_sales_fig.yaxis.axis_label = "Revenue"
country_sales_fig.yaxis.axis_label_text_color = palette[2]
counts_axis = LinearAxis(y_range_name="Units Sold",axis_label_text_color = palette[7],axis_label = "Units Sold")
country_sales_fig.add_layout(counts_axis,"left")

country_sales_fig.xaxis.axis_label = "Buyer Country"
country_sales_fig.xaxis.major_label_orientation = 3.14/16

country_sales_fig.add_tools(HoverTool(tooltips=tooltips_product_count, renderers=[units_by_country_bars]))
country_sales_fig.add_tools(HoverTool(tooltips=tooltips_revenue, renderers=[revenue_by_country_bars]))

country_sales_fig.legend.click_policy = 'hide'
country_sales_fig.legend.location='top_left'
show(country_sales_fig)

In [ ]:
mean_rating_per_country = per_country[per_country['Date']=='2021-09-30'][['Country','Total Average Rating']]
rating_per_country = ColumnDataSource(mean_rating_per_country)
rating_per_country_fig = figure(x_range = rating_per_country.data['Country'], title = "Rating per Country", x_axis_label = "Rating Country", y_axis_label = "Rating (Out of 5)", height=200, width=1600, tools=tools)
rating_by_country_bars = rating_per_country_fig.vbar(width = 0.9, source=rating_per_country, x = 'Country', top='Total Average Rating')
rating_per_country_fig.xaxis.major_label_orientation = 3.14/16

In [ ]:
country_sales_panel = TabPanel(child =  country_sales_fig, title = 'Per Country')
sku_id_sales_panel = TabPanel(child = skuid_sales_fig, title = 'Per SKU ID')
product_sales_panel = TabPanel(child = product_sales_fig, title = 'Per Product Title')
# rating_per_country_panel = TabPanel(child = rating_per_country_fig, title  = 'Country Ratings')

country_ratings_sales_tabs = Tabs(tabs = [country_sales_panel, sku_id_sales_panel,product_sales_panel])

#**CRASHES VS RATINGS**

In [ ]:
daily_avg_rating = ratings_per_day[ratings_per_day['Daily Average Rating'].notna()]
rating_and_crash = pd.merge(daily_avg_rating, crash_stats, on='Date')
rating_and_crash = rating_and_crash.loc[:,('Date','Daily Crashes','Daily Average Rating')]
rating_and_crash['Date'] = pd.to_datetime(rating_and_crash['Date'])
rating_and_crash = rating_and_crash.drop_duplicates()



In [ ]:
# RATING PER CRASHES PLOTTING
output_notebook()
source = ColumnDataSource(rating_and_crash)

tools = "wheel_zoom,box_zoom,pan,reset"
tooltips_date = [('Date','@Date{%F}')]

rating_crash_fig = figure(title = "Rating versus crashes", x_axis_label="Daily number of crashes", y_axis_label="Daily Average Rating", height=figure_height, width=figure_width, tools=tools)
rating_versus_crashes = rating_crash_fig.circle(color = palette[5],source = source, x = 'Daily Crashes', y = 'Daily Average Rating')

rating_crash_fig.add_tools(HoverTool(tooltips=tooltips_date, renderers=[rating_versus_crashes],formatters = {'@Date':'datetime'}))

show(rating_crash_fig)

In [ ]:
# NUMBER OF CRASHES VS TOTAL AVERAGE RATING
ratings_per_day["Date"] = pd.to_datetime(ratings_per_day["Date"])
ratings_per_day.sort_values(by = ["Date"], inplace = True)
# ratings_per_day = ratings_per_day.loc[:,("Total Average Rating")]

crash_stats["Date"] = pd.to_datetime(crash_stats["Date"])
crash_stats.sort_values(by=["Date"], inplace = True)
# crash_stats = crash_stats.loc[:, ("Daily Crashes")]

rating_and_crash_total = ratings_per_day.merge(crash_stats, on = 'Date',how = 'inner')
rating_and_crash_total = rating_and_crash_total.loc[:, ("Date","Total Average Rating", "Daily Crashes", "Daily ANRs","Daily Average Rating")]
rating_and_crash_total_indexed = rating_and_crash_total.set_index("Date")
rating_and_crash_total_indexed['Cumulative Crashes'] = rating_and_crash_total_indexed['Daily Crashes'].cumsum()
rating_and_crash_total_indexed



Total Average Rating  Daily Crashes  Daily ANRs  \
Date                                                          
2021-06-01                  4.15             15           1   
2021-06-02                  4.15             12           1   
2021-06-03                  4.15             20           1   
2021-06-04                  4.15             13           0   
2021-06-05                  4.15             14           0   
...                          ...            ...         ...   
2021-12-27                  4.14             64           0   
2021-12-28                  4.14             60           0   
2021-12-29                  4.14             37           0   
2021-12-30                  4.14             46           1   
2021-12-31                  4.14             50           0   

            Daily Average Rating  Cumulative Crashes  
Date                                                  
2021-06-01                   5.0                  15  
2021-06-02                   2.0                  27  
2021-06-03                   NaN                  47  
2021-06-04                   NaN                  60  
2021-06-05                   NaN                  74  
...                          ...                 ...  
2021-12-27                   NaN                4869  
2021-12-28                   4.0                4929  
2021-12-29                   NaN                4966  
2021-12-30                   NaN                5012  
2021-12-31                   5.0                5062  

[214 rows x 5 columns]

In [ ]:
# CUMULATIVE NUMBER OF CRASHES VS TOTAL AVERAGE RATING
ratings_per_day["Date"] = pd.to_datetime(ratings_per_day["Date"])
ratings_per_day.sort_values(by = ["Date"], inplace = True)
# ratings_per_day = ratings_per_day.loc[:,("Total Average Rating")]

crash_stats["Date"] = pd.to_datetime(crash_stats["Date"])
crash_stats.sort_values(by=["Date"], inplace = True)
# crash_stats = crash_stats.loc[:, ("Daily Crashes")]

rating_and_crash_total = ratings_per_day.merge(crash_stats, on = 'Date',how = 'inner')
rating_and_crash_total = rating_and_crash_total.loc[:, ("Date","Total Average Rating", "Daily Crashes", "Daily ANRs","Daily Average Rating")]
rating_and_crash_total_indexed = rating_and_crash_total.set_index("Date")
rating_and_crash_total_indexed['Cumulative Crashes'] = rating_and_crash_total_indexed['Daily Crashes'].cumsum()
rating_and_crash_total_indexed



Total Average Rating  Daily Crashes  Daily ANRs  \
Date                                                          
2021-06-01                  4.15             15           1   
2021-06-02                  4.15             12           1   
2021-06-03                  4.15             20           1   
2021-06-04                  4.15             13           0   
2021-06-05                  4.15             14           0   
...                          ...            ...         ...   
2021-12-27                  4.14             64           0   
2021-12-28                  4.14             60           0   
2021-12-29                  4.14             37           0   
2021-12-30                  4.14             46           1   
2021-12-31                  4.14             50           0   

            Daily Average Rating  Cumulative Crashes  
Date                                                  
2021-06-01                   5.0                  15  
2021-06-02                   2.0                  27  
2021-06-03                   NaN                  47  
2021-06-04                   NaN                  60  
2021-06-05                   NaN                  74  
...                          ...                 ...  
2021-12-27                   NaN                4869  
2021-12-28                   4.0                4929  
2021-12-29                   NaN                4966  
2021-12-30                   NaN                5012  
2021-12-31                   5.0                5062  

[214 rows x 5 columns]

In [ ]:
# CRASHES VS RATINGS LINE PLOT
source = ColumnDataSource(rating_and_crash_total_indexed)

output_notebook()
tools = "pan,wheel_zoom,box_zoom,reset"

tooltips_crashes = [('Daily Number of Crashes','@{Daily Crashes}'),('Date','@Date{%F}')]
total_tooltips_average_rating = [('Average Rating','@{Total Average Rating}'), ('Date','@Date{%F}')]
daily_tooltips_average_rating = [('Average Rating','@{Daily Average Rating}'), ('Date','@Date{%F}')]

total_crash_rate_fig = figure(title = "Cumulative Average Rating VS Number of Crashes", x_axis_label="Day", y_axis_label="Daily Crashes", x_axis_type = 'datetime', tools=tools, height = figure_height,width = figure_width)
daily_crash_rate_fig = figure(title = "Daily Average Rating VS Number of Crashes", x_axis_label="Day", y_axis_label="Daily Crashes", x_axis_type = 'datetime', tools=tools,height = figure_height,width = figure_width)


daily_crashes_line = total_crash_rate_fig.line(source=rating_and_crash_total_indexed, x = 'Date', y='Daily Crashes',color=palette[5],legend_label='Crashes',muted_alpha=0.1)
total_crashes_line = daily_crash_rate_fig.line(source=rating_and_crash_total_indexed, x = 'Date', y='Daily Crashes',color=palette[5],legend_label='Crashes',muted_alpha=0.1)


total_crash_rate_fig.extra_y_ranges['total_rating'] = Range1d(start =float(rating_and_crash_total_indexed['Total Average Rating'].min())*0.9, end = float(rating_and_crash_total_indexed['Total Average Rating'].max())*1.1)
daily_crash_rate_fig.extra_y_ranges['daily_rating'] = Range1d(start =float(rating_and_crash_total_indexed['Daily Average Rating'].min())*0.9,end = float(rating_and_crash_total_indexed['Daily Average Rating'].max())*1.1)
total_ratings_line = total_crash_rate_fig.line(y_range_name = 'total_rating',source=rating_and_crash_total_indexed, x = 'Date', y='Total Average Rating', color=palette[3],legend_label='Cumulative Rating',muted_alpha=0.1)
daily_ratings_line = daily_crash_rate_fig.scatter(y_range_name = 'daily_rating',source=rating_and_crash_total_indexed, x = 'Date', y='Daily Average Rating', color=palette[3],legend_label='Daily Rating',muted_alpha=0.1)

total_crash_rate_fig.yaxis.axis_label = "Daily Crashes"
total_crash_rate_fig.yaxis.axis_label_text_color = palette[5]
daily_crash_rate_fig.yaxis.axis_label = "Daily Crashes"
daily_crash_rate_fig.yaxis.axis_label_text_color = palette[5]

total_rating_axis = LinearAxis(y_range_name='total_rating',axis_label_text_color = palette[3],axis_label = "Cumulative Average Rating")
daily_rating_axis = LinearAxis(y_range_name='daily_rating',axis_label_text_color = palette[3],axis_label = "Daily Average Rating")
total_crash_rate_fig.add_layout(total_rating_axis,"left")
daily_crash_rate_fig.add_layout(daily_rating_axis,"left")

total_crash_rate_fig.xaxis.axis_label = "Date"
daily_crash_rate_fig.xaxis.axis_label = "Date"

total_crash_rate_fig.add_tools(HoverTool(tooltips=tooltips_crashes, renderers=[daily_crashes_line], formatters = {'@Date':'datetime'}))
total_crash_rate_fig.add_tools(HoverTool(tooltips=total_tooltips_average_rating, renderers=[total_ratings_line], formatters = {'@Date':'datetime'}))
total_crash_rate_fig.legend.click_policy = 'mute'
total_crash_rate_fig.legend.location = 'top_left'
show(total_crash_rate_fig)

daily_crash_rate_fig.add_tools(HoverTool(tooltips=tooltips_crashes, renderers=[total_crashes_line], formatters = {'@Date':'datetime'}))
daily_crash_rate_fig.add_tools(HoverTool(tooltips=daily_tooltips_average_rating, renderers=[daily_ratings_line], formatters = {'@Date':'datetime'}))
daily_crash_rate_fig.legend.click_policy = 'mute'
daily_crash_rate_fig.legend.location = 'bottom_right'
show(daily_crash_rate_fig)


In [ ]:
ratings_crashes_panel = TabPanel(child = rating_crash_fig, title='Ratings vs Crashes')
ratings_crashes_daily_panel = TabPanel(child=daily_crash_rate_fig, title='Daily Ratings')
rating_crashes_monthly_panel = TabPanel(child=total_crash_rate_fig,title = 'Total Ratings')

# Assign the panels to Tabs
crash_tabs = Tabs(tabs=[ratings_crashes_daily_panel,rating_crashes_monthly_panel,ratings_crashes_panel])

# Show the tabbed layout

In [ ]:
# revenue_panel = TabPanel(child = plot_bokeh_map_by_day(cumulative_sales_per_day_choropleth, "Cumulative Sales Revenue per Day", color_mapper_range=(0, 500), palette=cc.CET_L12), title='Cumulative Sales Revenue per Day')
# monthly_ratings_panel = TabPanel(child=plot_bokeh_map_by_month(choropleth_ratings, "Country Ratings Per Month", palette=brewer['BuGn'][5][::-1], months=["June", "July", "August", "September", "October", "November", "December"], color_mapper_range=(0, 5)), title='Average Monthly Rating')
# total_ratings_panel = TabPanel(child=plot_bokeh_map_static(average_country_rating_cloropleth, "Average Country Rating", "Average Rating", palette=brewer['BuGn'][5][::-1]),title = 'Total Average Rating')


# # Assign the panels to Tabs
# map_tabs = Tabs(tabs=[total_ratings_panel,revenue_panel, monthly_ratings_panel])

# # Show the tabbed layout
# show(map_tabs)

# **REPORT QUERIES**

The following cells are for extracting insights from the data, explained in the report. Please run them in order if you wish to see the descriptive statistics described in parts 3 and 4 of the report.

Otherwise, skipping these cells and running only the last one produces the dashboard.

In [ ]:
# Query 1: Average Rating per Continent
continent_ratings = average_country_rating.merge(country_codes, how = 'outer', left_on='Country', right_on='alpha-2')
average_continent_ratings = continent_ratings.groupby('region').mean(numeric_only = True)
average_continent_ratings

Average Rating
region                  
Africa          3.841972
Americas        4.148137
Asia            4.407522
Europe          4.438111
Oceania         4.541154

In [ ]:
# Query 2: Daily ratings per continent
continent_daily_ratings = per_country[per_country["Daily Average Rating"].notna()].merge(country_codes, how = 'outer', left_on = 'Country', right_on = 'alpha-2')
continent_daily_ratings_summary = continent_daily_ratings.groupby('region').mean(numeric_only = True).sort_values(by = "Daily Average Rating")
continent_daily_ratings_summary["Total Daily Reviews per Region"] = continent_daily_ratings.loc[:,["Daily Average Rating", "region"]].groupby('region').count()
continent_daily_ratings_summary

Daily Average Rating  Total Average Rating  \
region                                                 
Americas              3.615385              4.062885   
Europe                3.625000              4.239375   
Oceania               4.000000              4.190000   
Asia                  4.600000              4.558000   
Africa                     NaN                   NaN   

          Total Daily Reviews per Region  
region                                    
Americas                              52  
Europe                                16  
Oceania                                2  
Asia                                   5  
Africa                                 0

In [ ]:
# Query 3: Counts of daily ratings by score, per country over the period
lowest_ratings = per_country.sort_values(by = 'Daily Average Rating')
lowest_ratings_by_country = per_country.loc[:,["Country","Daily Average Rating","Total Average Rating"]].groupby(["Country", "Daily Average Rating"]).count()
lowest_ratings_by_country = lowest_ratings_by_country.rename(columns = {"Total Average Rating":"Count of Score"})
lowest_ratings_by_country_sorted = lowest_ratings_by_country.sort_values(by = ['Daily Average Rating', 'Count of Score'])
lowest_ratings_by_country_sorted


Count of Score
Country Daily Average Rating                
FR      1.0                                2
GB      1.0                                2
US      1.0                                7
GR      2.0                                1
US      2.0                                5
AT      3.0                                1
AU      3.0                                1
BR      3.0                                1
PH      3.0                                1
CA      3.0                                2
US      3.0                                8
AR      4.0                                1
CA      4.0                                1
RU      4.0                                1
US      4.0                                4
        4.5                                2
AU      5.0                                1
CA      5.0                                1
CO      5.0                                1
DE      5.0                                1
ES      5.0                                1
FR      5.0                                1
ID      5.0                                1
IR      5.0                                1
PH      5.0                                1
SK      5.0                                1
TR      5.0                                1
GR      5.0                                2
GB      5.0                                3
US      5.0                               19

In [ ]:
# Query 4: Frequency table of ratings per country registered over the period
count_of_scores_by_country = per_country.loc[:,["Country","Daily Average Rating"]].groupby(["Country"]).count()
count_of_scores_by_country = count_of_scores_by_country.rename(columns = {"Daily Average Rating":"Review Counts"})
print(count_of_scores_by_country.loc["FR"])
sorted_score_counts = count_of_scores_by_country.sort_values(by = "Review Counts", ascending = False)
sorted_score_counts.head(n = 35)


Review Counts    3
Name: FR, dtype: int64


Review Counts
Country               
US                  45
GB                   5
CA                   4
GR                   3
FR                   3
AU                   2
PH                   2
SK                   1
ES                   1
ID                   1
DE                   1
RU                   1
CO                   1
AR                   1
IR                   1
TR                   1
BR                   1
AT                   1
PE                   0
MD                   0
MT                   0
PK                   0
MX                   0
MY                   0
NI                   0
PL                   0
NZ                   0
NO                   0
NL                   0
MZ                   0
PA                   0
PW                   0
PR                   0
SV                   0
VN                   0

In [ ]:
# Query 5: Sales volume for low-rating countries in North America (Dominican Republic and Guatemala)
sales_by_country_per_day_temp = sales_by_country_per_day.loc[:,["Buyer Country", "Amount (Merchant Currency)"]].groupby(['Buyer Country'], dropna = False).count()
sales_by_country_per_day_temp = sales_by_country_per_day_temp.rename(columns = {"Amount (Merchant Currency)": "Units Sold"})
sales_all_countries = country_codes.merge(sales_by_country_per_day_temp, left_on='alpha-2', right_on = 'Buyer Country', how = 'outer')
sales_all_countries = sales_all_countries.fillna(0)
sales_all_countries = sales_all_countries.set_index("alpha-2")
sales_DO = sales_all_countries.loc["DO"]
print(sales_DO)
sales_GT = sales_all_countries.loc["GT"]
print(sales_GT)
sales_all_countries_sorted = sales_all_countries.sort_values(by = "Units Sold", ascending = False)
sales_all_countries_sorted.head(n=50)

name          Dominican Republic
alpha-3                      DOM
region                  Americas
Units Sold                   0.0
Name: DO, dtype: object
name          Guatemala
alpha-3             GTM
region         Americas
Units Sold          0.0
Name: GT, dtype: object


name alpha-3    region  \
alpha-2                                                                        
US                                United States of America     USA  Americas   
GB       United Kingdom of Great Britain and Northern I...     GBR    Europe   
CA                                                  Canada     CAN  Americas   
DE                                                 Germany     DEU    Europe   
NL                                             Netherlands     NLD    Europe   
AU                                               Australia     AUS   Oceania   
IT                                                   Italy     ITA    Europe   
SE                                                  Sweden     SWE    Europe   
MX                                                  Mexico     MEX  Americas   
GR                                                  Greece     GRC    Europe   
BR                                                  Brazil     BRA  Americas   
RU                                      Russian Federation     RUS    Europe   
CZ                                                 Czechia     CZE    Europe   
BE                                                 Belgium     BEL    Europe   
DK                                                 Denmark     DNK    Europe   
PL                                                  Poland     POL    Europe   
UA                                                 Ukraine     UKR    Europe   
AT                                                 Austria     AUT    Europe   
FR                                                  France     FRA    Europe   
PH                                             Philippines     PHL      Asia   
ES                                                   Spain     ESP    Europe   
PT                                                Portugal     PRT    Europe   
CH                                             Switzerland     CHE    Europe   
IE                                                 Ireland     IRL    Europe   
NZ                                             New Zealand     NZL   Oceania   
CR                                              Costa Rica     CRI  Americas   
PR                                             Puerto Rico     PRI  Americas   
ID                                               Indonesia     IDN      Asia   
CO                                                Colombia     COL  Americas   
ZA                                            South Africa     ZAF    Africa   
MY                                                Malaysia     MYS      Asia   
TR                                                  Turkey     TUR      Asia   
LT                                               Lithuania     LTU    Europe   
NO                                                  Norway     NOR    Europe   
BG                                                Bulgaria     BGR    Europe   
FI                                                 Finland     FIN    Europe   
IL                                                  Israel     ISR      Asia   
AR                                               Argentina     ARG  Americas   
PN                                                Pitcairn     PCN   Oceania   
PS                                     Palestine, State of     PSE      Asia   
YT                                                 Mayotte     MYT    Africa   
PA                                                  Panama     PAN  Americas   
PG                                        Papua New Guinea     PNG   Oceania   
PY                                                Paraguay     PRY  Americas   
PE                                                    Peru     PER  Americas   
MU                                               Mauritius     MUS    Africa   
MQ                                              Martinique     MTQ  Americas   
MR                                              Mauritania     MRT    Africa   
PK                                                Paki

In [ ]:
# Query 6: Units sold over the period and daily ratings for Mexico
mexico_sales = sales_all_countries.loc["MX"]
mexico_daily_ratings = sorted_score_counts.loc["MX"]
print(mexico_daily_ratings)
mexico_sales

Review Counts    0
Name: MX, dtype: int64


name            Mexico
alpha-3            MEX
region        Americas
Units Sold        10.0
Name: MX, dtype: object

In [ ]:
# Query 7: Units sold over the period and daily ratings for Canada
canada_sales = sales_all_countries.loc["CA"]
canada_daily_ratings = lowest_ratings_by_country_sorted.loc["CA"]
print(canada_daily_ratings)
canada_sales

                      Count of Score
Daily Average Rating                
3.0                                2
4.0                                1
5.0                                1


name            Canada
alpha-3            CAN
region        Americas
Units Sold        70.0
Name: CA, dtype: object

In [ ]:
# Query YOUROWN: Units sold over the period and daily ratings for any country of your choosing. Please uncomment and add your own alpha-2 to use this query.
# custom_country_sales = sales_all_countries.loc["enter alpha-2 here"]
# custom_country_daily_ratings = lowest_ratings_by_country_sorted.loc["enter alpha-2 here"]
# print(custom_country_sales)
# print(custom_country_daily_ratings)

In [ ]:
# Query 8: New Reviews for clients in South America
argentina_sales = sales_all_countries.loc["AR"]
argentina_daily_ratings = lowest_ratings_by_country_sorted.loc["AR"]
print(argentina_sales)
print(argentina_daily_ratings)
brazil_sales = sales_all_countries.loc["BR"]
brazil_daily_ratings = lowest_ratings_by_country_sorted.loc["BR"]
print(brazil_sales)
print(brazil_daily_ratings)

name          Argentina
alpha-3             ARG
region         Americas
Units Sold          1.0
Name: AR, dtype: object
                      Count of Score
Daily Average Rating                
4.0                                1
name            Brazil
alpha-3            BRA
region        Americas
Units Sold         7.0
Name: BR, dtype: object
                      Count of Score
Daily Average Rating                
3.0                                1


In [ ]:
# Query 9: Download volume in most and least satisfied countries in Africa
egypt_sales = sales_all_countries.loc["EG"]
print(egypt_sales)
botswana_sales = sales_all_countries.loc["BW"]
print(botswana_sales)

name           Egypt
alpha-3          EGY
region        Africa
Units Sold       0.0
Name: EG, dtype: object
name          Botswana
alpha-3            BWA
region          Africa
Units Sold         0.0
Name: BW, dtype: object


In [ ]:
# Query 10: Download volume in most and least satisfied countries in Asia
turkey_sales = sales_all_countries.loc["TR"]
iran_sales = sales_all_countries.loc["IR"]
indonesia_sales = sales_all_countries.loc["ID"]
china_sales = sales_all_countries.loc["CN"]
iraq_sales = sales_all_countries.loc["IQ"]
print(turkey_sales)
print(iran_sales)
print(indonesia_sales)
print(china_sales)
print(iraq_sales)

name          Turkey
alpha-3          TUR
region          Asia
Units Sold       2.0
Name: TR, dtype: object
name          Iran (Islamic Republic of)
alpha-3                              IRN
region                              Asia
Units Sold                           0.0
Name: IR, dtype: object
name          Indonesia
alpha-3             IDN
region             Asia
Units Sold          2.0
Name: ID, dtype: object
name          China
alpha-3         CHN
region         Asia
Units Sold      0.0
Name: CN, dtype: object
name          Iraq
alpha-3        IRQ
region        Asia
Units Sold     0.0
Name: IQ, dtype: object


In [ ]:
# Query 11: Download volume and ratings in most and least satisfied countries in Europe
germany_sales = sales_all_countries.loc["DE"]
spain_sales = sales_all_countries.loc["ES"]
france_daily_ratings = lowest_ratings_by_country_sorted.loc["FR"]
france_sales = sales_all_countries.loc["FR"]

# germany_sales
# spain_sales
# france_daily_ratings
france_sales

name          France
alpha-3          FRA
region        Europe
Units Sold       3.0
Name: FR, dtype: object

In [ ]:
# Query 12: Download volume in most and least satisfied countries in Oceania
australia_daily_ratings = lowest_ratings_by_country_sorted.loc["AU"]
australia_sales = sales_all_countries.loc["AU"]
new_zealand_sales = sales_all_countries.loc["NZ"]

# australia_daily_ratings
# australia_sales
new_zealand_sales

name          New Zealand
alpha-3               NZL
region            Oceania
Units Sold            2.0
Name: NZ, dtype: object

In [ ]:
# Query 13: Reviews mentioning a crash
pd.set_option('display.max_colwidth', None)
new_reviews = reviews.loc[:, ["Review Text", "Developer Reply Text", "Review Submit Date and Time", "Star Rating", "Device"]]
new_reviews = new_reviews.drop_duplicates(["Review Submit Date and Time"])
review_samples = new_reviews[new_reviews["Review Text"].notna()].sort_values(by = ["Star Rating"]).set_index("Review Submit Date and Time")
reviews_mentioning_crash = review_samples[review_samples["Review Text"].str.contains("crash")]

reviews_mentioning_crash["Review Text"]


Review Submit Date and Time
2021-07-13T09:53:46Z                                                                              Maybe it's my phone but constant crashes make this unusable... Uninstall.
2021-08-17T03:02:29Z    Purchased the dm tools, dm initiative tracker doesn't go back pages only forward and periodically crashes. Don't waste your money, this is garbage.
Name: Review Text, dtype: object

In [ ]:
# Query 14: Bad Reviews and Developer replies
bad_reviews = review_samples[review_samples["Star Rating"] == 1]
bad_reviews["Review Text"]
# bad_reviews["Developer Reply Text"]

Review Submit Date and Time
2021-06-22T12:39:50Z                                                                                                                           Has jack rabbit for recource
2021-07-13T09:53:46Z                                                                              Maybe it's my phone but constant crashes make this unusable... Uninstall.
2021-07-29T22:30:01Z                                                                                                      Just like all the others you've tried dont bother
2021-09-02T16:03:37Z                                                                                              Better apps to be using, hardly has phb information in it
2021-11-25T01:52:00Z                                                           This app has been down for two weeks now. Such a bummer was my go to app. Happy thanksgiving
2021-08-17T03:02:29Z    Purchased the dm tools, dm initiative tracker doesn't go back pages only forward and per

In [ ]:
# Query 15: Reviews from November and December
reviews_end_of_year = review_samples.reset_index(names = "Review Date and Time")
reviews_end_of_year["Review Date and Time"] = pd.to_datetime(reviews_end_of_year["Review Date and Time"])
reviews_end_of_year = reviews_end_of_year[reviews_end_of_year["Review Date and Time"].dt.month >= 11]
reviews_end_of_year = reviews_end_of_year.sort_values(by="Review Date and Time")
reviews_end_of_year

Review Date and Time  \
21 2021-11-04 22:14:45+00:00   
18 2021-11-09 04:53:13+00:00   
19 2021-11-17 20:50:13+00:00   
30 2021-11-20 23:49:19+00:00   
20 2021-11-21 12:59:42+00:00   
4  2021-11-25 01:52:00+00:00   
27 2021-11-25 04:32:37+00:00   
22 2021-12-05 05:50:14+00:00   
23 2021-12-05 21:38:20+00:00   
24 2021-12-28 14:19:58+00:00   
28 2021-12-31 13:21:49+00:00   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     Review Text  \
21                                                                                                                                                                                                                                                                                                                                                                                                             Приложение выглядит очень удобным, но очень сильно печалит, что нет русского языка, но 4 поставлю   
18                                                                                                                                                                                      I used to really like this app when new content was added to the forums fairly regularly but right now it's missing a lot of information from the newer books. It used to be my go to reference because it had all the current info but now they've neglected to upload new content to the forums for several books now.   
19                                                                                                                                                                                    Awkwardly missing wood elves, drow, cleric domains ect.... So you're saying a "complete reference" can miss come content I need to rummage on some internet forms to collect?.... Don't get me wrong, being able to import and add information is a great feature and full credit to you. But you're not complete are you?   
30                                                                                                                                                                                                                                                                                                                                                                                                        The newest update fixed it, re downloaded the additional content and so far it works great once again!   
20                                                                                                                                                                                                                                                                                                                                                                                                                              I did what you told me to uninstall n re instal it but it still did not work. :(   
4                                                                                                                                                                                                                                                                                                                                                                                                                   This app has been down for two weeks now. Such a bummer was my go to app. Happy thanksgiving   
27                                                                                                                         

In [ ]:
# Query 16: Developer Replies and phone codenames
developer_replies = reviews.loc[:, ["Review Text", "Developer Reply Text", "Review Submit Date and Time", "Star Rating", "Developer Reply Date and Time"]]
developer_replies = review_samples.reset_index(names = "Developer Reply Date and Time")
developer_replies["Developer Reply Date and Time"] = pd.to_datetime(developer_replies["Developer Reply Date and Time"])
developer_replies = developer_replies[developer_replies["Developer Reply Date and Time"].dt.month >= 11]
developer_replies = developer_replies.sort_values(by = "Developer Reply Date and Time")
developer_replies

Developer Reply Date and Time  \
21     2021-11-04 22:14:45+00:00   
18     2021-11-09 04:53:13+00:00   
19     2021-11-17 20:50:13+00:00   
30     2021-11-20 23:49:19+00:00   
20     2021-11-21 12:59:42+00:00   
4      2021-11-25 01:52:00+00:00   
27     2021-11-25 04:32:37+00:00   
22     2021-12-05 05:50:14+00:00   
23     2021-12-05 21:38:20+00:00   
24     2021-12-28 14:19:58+00:00   
28     2021-12-31 13:21:49+00:00   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     Review Text  \
21                                                                                                                                                                                                                                                                                                                                                                                                             Приложение выглядит очень удобным, но очень сильно печалит, что нет русского языка, но 4 поставлю   
18                                                                                                                                                                                      I used to really like this app when new content was added to the forums fairly regularly but right now it's missing a lot of information from the newer books. It used to be my go to reference because it had all the current info but now they've neglected to upload new content to the forums for several books now.   
19                                                                                                                                                                                    Awkwardly missing wood elves, drow, cleric domains ect.... So you're saying a "complete reference" can miss come content I need to rummage on some internet forms to collect?.... Don't get me wrong, being able to import and add information is a great feature and full credit to you. But you're not complete are you?   
30                                                                                                                                                                                                                                                                                                                                                                                                        The newest update fixed it, re downloaded the additional content and so far it works great once again!   
20                                                                                                                                                                                                                                                                                                                                                                                                                              I did what you told me to uninstall n re instal it but it still did not work. :(   
4                                                                                                                                                                                                                                                                                                                                                                                                                   This app has been down for two weeks now. Such a bummer was my go to app. Happy thanksgiving   
27                                                                    

In [ ]:
# Query 17: Cumulative downloads to date for countries with the highest volume of downloads (8 top markets)
cumulative_transactions_per_country_p_sorted.head(n = 8)


Transaction Date  2021-06-01  2021-06-02  2021-06-03  2021-06-04  2021-06-05  \
Buyer Country                                                                  
US                         2           9          15          21          23   
GB                         0           1           1           1           1   
CA                         0           0           0           0           0   
DE                         0           0           0           0           0   
NL                         0           0           0           1           1   
AU                         0           0           0           0           0   
IT                         0           0           0           0           0   
SE                         0           1           1           1           1   

Transaction Date  2021-06-06  2021-06-07  2021-06-08  2021-06-09  2021-06-10  \
Buyer Country                                                                  
US                        36          48          50          54          55   
GB                         1           1           2           2           2   
CA                         0           0           0           0           0   
DE                         0           0           0           0           0   
NL                         1           1           1           1           1   
AU                         0           1           1           1           1   
IT                         0           0           0           0           0   
SE                         1           1           1           1           1   

Transaction Date  ...  2021-12-22  2021-12-23  2021-12-24  2021-12-25  \
Buyer Country     ...                                                   
US                ...        1262        1265        1269        1273   
GB                ...         104         104         106         106   
CA                ...          65          66          66          67   
DE                ...          47          47          47          47   
NL                ...          25          26          26          26   
AU                ...          25          25          25          25   
IT                ...          13          13          13          13   
SE                ...          10          10          11          11   

Transaction Date  2021-12-26  2021-12-27  2021-12-28  2021-12-29  2021-12-30  \
Buyer Country                                                                  
US                      1277        1285        1290        1297        1301   
GB                       108         109         109         109         109   
CA                        67          69          69          69          70   
DE                        47          47          47          47          47   
NL                        26          26          26          26          26   
AU                        25          25          25          25          25   
IT                        13          13          13          13          13   
SE                        11          11          11          11          11   

Transaction Date  2021-12-31  
Buyer Country                 
US                      1308  
GB                       110  
CA                        70  
DE                        47  
NL                        26  
AU                        25  
IT                        13  
SE                        11  

[8 rows x 214 columns]

In [ ]:
# Query 18: Daily Ratings UK
uk_daily_ratings = lowest_ratings_by_country_sorted.loc["GB"]
uk_daily_ratings

Count of Score
Daily Average Rating                
1.0                                2
5.0                                3

**LAYOUTING**

In [ ]:
title_color = palette[0] # 0=grey 1=bronze 2=yellow 3=green 4=pink 5=purple 6=orange,7=blue-green
heading_color = palette[5]
padding_color = palette[2]
border_color = palette[7]

title_style = {
    'text-align':'center',
    'color':title_color,
    'font-size':'1.1rem',
    'font-family':'Monaco',
    'font-weight':'600',
    }

widget_heading_style ={
    'font-family':'Monaco',
    'color':heading_color,
}

widget_styles = {
    'border-color':border_color,
}

title_html = """<h1>App Summary</h1>
<h3>Analytics of the Complete Reference for
Dungeons and Dragons 5
</h3>
"""
downloads_text = """<h2>Downloads<h2>"""
map_text = """<h2>Worldwide Data</h2>"""
crash_text = """<h2>Ratings and Stability</h2>"""
sales_text = """<h2>Sales</h2>"""
seg_text = """<h2>Sales by Attributes</h2>"""

title = Div(text=title_html, width = 1200, styles = title_style)
pn.extension()

map_heading = Div(text = map_text,styles = widget_heading_style, height = 50)
crash_heading = Div(text = crash_text,  styles = widget_heading_style,height = 50)
sales_heading = Div(text = sales_text, styles = widget_heading_style,height = 50)
seg_heading = Div(text = seg_text, styles = widget_heading_style,height = 50)

map_widget = bokeh_column(map_heading,map_tabs,styles = widget_styles, align = ('center'),margin = (50,0),height = figure_height+map_heading.height)
crash_widget = bokeh_column(crash_heading,crash_tabs,styles = widget_styles, align = ('center'),margin = (50,0), height = figure_height+crash_heading.height)
sales_widget = bokeh_column(sales_heading,sales_tabs,styles = widget_styles, align = ('center'),margin = (50,0), height = figure_height+sales_heading.height)
seg_widget = bokeh_column(seg_heading,country_ratings_sales_tabs,styles = widget_styles, align = ('center'),margin = (50,0), height = figure_height+seg_heading.height)

# widgets = pn.FlexBox(downloads_widget, map_widget,crash_widget,sales_widget,seg_widget,flex_wrap = "wrap",sizing_mode="scale_width",justify_content='spaced-evenly')
dashboard = pn.Column(title,map_widget,crash_widget,sales_widget,seg_widget, styles = dict(margin = "0 auto"))

dashboard.save('dashboard_submission.html')
# dashboard

NameError: name 'palette' is not defined